In [171]:
# Julia 0.7
using CSV, DataFrames, Gadfly, Statistics, LinearAlgebra, GLM, CategoricalArrays, MLBase

In [172]:
function MatriceVariablesExplicatives(trainSample)
    JP = collect(trainSample[:,:JP_Sales])
    Other = collect(trainSample[:,:Other_Sales])
    CriticScore = ScoreFormatting(collect(trainSample[:,:Critic_Score]))
    CriticCount = ScoreFormatting(collect(trainSample[:,:Critic_Count]))
    UserScore = ScoreFormatting(collect(trainSample[:,:User_Score]))
    UserCount = ScoreFormatting(collect(trainSample[:,:User_Count]))
    n = size(JP,1)
    X = hcat(ones(n),JP,Other,CriticScore,CriticCount,UserScore,UserCount)
    return X
end

MatriceVariablesExplicatives (generic function with 1 method)

In [173]:
function ScoreFormatting(trainSample)
    scoreMean=floor(mean(collect(skipmissing(trainSample))))
    for i in eachindex(trainSample)
        if ismissing(trainSample[i])
            trainSample[i] = scoreMean
        end
    end
    return trainSample
end

ScoreFormatting (generic function with 1 method)

In [174]:
function RMSE(testSample,predictions)
    
    GlobalPredictions = collect(predictions[:Global_Sales])
    GlobalTest = collect(testSample[:Global_Sales])
    
    N = size(GlobalTest,2)
    somme = 0
    for i in 1:N
        somme = somme + (GlobalPredictions[i] - GlobalTest[i])^2
    end
    
    RMSE_Globale = sqrt(somme / N)
    
    NAPredictions = collect(predictions[:NA_Sales]
    NATest = testSample[:NA_Sales]
    
    somme = 0
    for i in 1:N
        somme = somme + (NAPredictions[i] - NATest[i])^2
    end
    
    RMSE_NA = sqrt(somme / N)
    RMSEMean = (RMSE_NA + RMSE_Globale)/2
    return RMSEMean
end

LoadError: syntax: missing comma or ) in argument list

In [175]:
train = CSV.read("train.csv")

14094×16 DataFrame. Omitted printing of 15 columns
│ Row   │ ID     │
│       │ Int64⍰ │
├───────┼────────┤
│ 1     │ 1      │
│ 2     │ 2      │
│ 3     │ 3      │
│ 4     │ 4      │
│ 5     │ 5      │
│ 6     │ 6      │
│ 7     │ 7      │
│ 8     │ 8      │
│ 9     │ 9      │
│ 10    │ 10     │
⋮
│ 14084 │ 14084  │
│ 14085 │ 14085  │
│ 14086 │ 14086  │
│ 14087 │ 14087  │
│ 14088 │ 14088  │
│ 14089 │ 14089  │
│ 14090 │ 14090  │
│ 14091 │ 14091  │
│ 14092 │ 14092  │
│ 14093 │ 14093  │
│ 14094 │ 14094  │

In [176]:
allIndexes = convert(Array{Int64},collect(train[1]))

14094-element Array{Int64,1}:
     1
     2
     3
     4
     5
     6
     7
     8
     9
    10
    11
    12
    13
     ⋮
 14083
 14084
 14085
 14086
 14087
 14088
 14089
 14090
 14091
 14092
 14093
 14094

In [177]:
NA_Sales = collect(train[:,:NA_Sales])
Global_Sales = collect(train[:,:Global_Sales])
Other_Sales = collect(train[:,:Other_Sales])
JP_Sales = collect(train[:,:JP_Sales])
Critic_Score = collect(train[:,:Critic_Score])
Critic_Count = collect(train[:,:Critic_Count])
User_Score = collect(train[:,:User_Score])
User_Count = collect(train[:,:User_Count])

##Critic score, User Score, Critic count, User Count 
moyenneCriticCount = floor(mean(collect(skipmissing(train[:,:Critic_Count]))))
moyenneCriticScore =floor(mean(collect(skipmissing(train[:,:Critic_Score]))))
moyenneUser_Score = floor(mean(collect(skipmissing(train[:,:User_Score]))))
moyenneUser_Count = floor(mean(collect(skipmissing(train[:,:User_Count]))))

157.0

In [178]:
trainIndexes = collect(Kfold(size(train,1), 10))

#Contiendra les 10 echantillons de training
trainSamples = []

#Contiendra les 10 echantillons de test
testSamples = []

for i=1:size(trainIndexes,1)
    sampleTrain = similar(train,0)
    sampleTest = similar(train,0)
    
    #Set up les 
    testIndexes = setdiff(allIndexes,trainIndexes[i])
    
    for k in eachindex(testIndexes)
        sampleTest = vcat(sampleTest, train[testIndexes[k],:])
    end
    
    for j in eachindex(trainIndexes[i])
      index = trainIndexes[i][j]
      sampleTrain = vcat(sampleTrain, train[index,:])
    end
    
    push!(trainSamples, sampleTrain)
    push!(testSamples, sampleTest)
end



In [179]:
trainSamples[1]

12685×16 DataFrame. Omitted printing of 14 columns
│ Row   │ ID     │ Name                                                  │
│       │ Int64⍰ │ Union{Missing, String}                                │
├───────┼────────┼───────────────────────────────────────────────────────┤
│ 1     │ 1      │ Zoo Keeper                                            │
│ 2     │ 3      │ Power Play Pool                                       │
│ 3     │ 4      │ SpongeBob SquarePants: Revenge of the Flying Dutchman │
│ 4     │ 5      │ Deception IV: Blood Ties                              │
│ 5     │ 6      │ Binary Domain                                         │
│ 6     │ 7      │ Jikkyou Powerful Pro Yakyuu 3 '97 Haru                │
│ 7     │ 10     │ Buzz! Junior: Jungle Party                            │
│ 8     │ 11     │ Battlefield 3                                         │
│ 9     │ 12     │ Monster High 13 Wishes                                │
│ 10    │ 13     │ Barbie: Race & Ride                                   │
⋮
│ 12675 │ 14081  │ Big Mutha Truckers                                    │
│ 12676 │ 14082  │ Batman Forever: The Arcade Game                       │
│ 12677 │ 14083  │ Teenage Mutant Ninja Turtles (3DS)                    │
│ 12678 │ 14084  │ Jak and Daxter: The Lost Frontier                     │
│ 12679 │ 14085  │ My Baby 3 & Friends                                   │
│ 12680 │ 14086  │ Assault Rigs                                          │
│ 12681 │ 14087  │ NHL 16                                                │
│ 12682 │ 14089  │ The Urbz: Sims in the City (all regions sales)        │
│ 12683 │ 14091  │ Saint                                                 │
│ 12684 │ 14093  │ Fishdom 2 Deluxe                                      │
│ 12685 │ 14094  │ Littlest Pet Shop                                     │

In [180]:
RMSETotal = []
Beta1Total = []
Beta2Total = []
for i in eachindex(trainSamples)
    
    #TRAIN
    X = MatriceVariablesExplicatives(trainSamples[i])
    β̂₁ = (X'X)\X'trainSamples[i][:,:NA_Sales]
    β̂₂ = (X'X)\X'trainSamples[i][:,:Global_Sales]
    push!(Beta1Total,β̂₁)
    push!(Beta2Total,β̂₂)
    #TEST
    Xtest = MatriceVariablesExplicatives(testSamples[i])
    Na_SalesTest = Xtest * β̂₁
    Global_SalesTest = Xtest * β̂₂
    
    predictionsTest = DataFrame(NA_Sales = Na_SalesTest,Global_Sales = Global_SalesTest)
    RMSEResult = RMSE(testSamples[i], predictionsTest) 
    RMSETotal = push!(RMSETotal,RMSEResult)
end
RMSETotal
Beta1Total=mean(Beta1Total)
Beta2Total=mean(Beta2Total)

7-element Array{Float64,1}:
 -0.2508221625202939    
  2.1898096094879795    
  4.918784610258663     
  0.0054968796601540665 
  0.004311619750196609  
 -0.018541826245530395  
  0.00014961997028575545

In [181]:
test = CSV.read("test.csv")

2490×13 DataFrame. Omitted printing of 9 columns
│ Row  │ ID     │ Platform │ Year_of_Release │ Genre        │
│      │ Int64⍰ │ String⍰  │ Int64⍰          │ String⍰      │
├──────┼────────┼──────────┼─────────────────┼──────────────┤
│ 1    │ 14095  │ GBA      │ 2002            │ Fighting     │
│ 2    │ 14096  │ PS3      │ 2008            │ Action       │
│ 3    │ 14097  │ N64      │ 1997            │ Sports       │
│ 4    │ 14098  │ GC       │ 2002            │ Fighting     │
│ 5    │ 14099  │ X360     │ 2010            │ Role-Playing │
│ 6    │ 14100  │ DS       │ 2009            │ Adventure    │
│ 7    │ 14101  │ DS       │ 2005            │ Simulation   │
│ 8    │ 14102  │ PS2      │ 2004            │ Role-Playing │
│ 9    │ 14103  │ PS2      │ 2006            │ Fighting     │
│ 10   │ 14104  │ PC       │ 2011            │ Puzzle       │
⋮
│ 2480 │ 16574  │ X360     │ 2015            │ Action       │
│ 2481 │ 16575  │ PS3      │ 2010            │ Racing       │
│ 2482 │ 16576  │ PS       │ 1996            │ Action       │
│ 2483 │ 16577  │ PS3      │ 2012            │ Shooter      │
│ 2484 │ 16578  │ GBA      │ 2002            │ Sports       │
│ 2485 │ 16579  │ XB       │ 2006            │ Sports       │
│ 2486 │ 16580  │ Wii      │ 2007            │ Adventure    │
│ 2487 │ 16581  │ PS2      │ 2006            │ Adventure    │
│ 2488 │ 16582  │ GC       │ 2002            │ Strategy     │
│ 2489 │ 16583  │ X360     │ 2011            │ Fighting     │
│ 2490 │ 16584  │ DS       │ 2008            │ Sports       │

In [184]:

Other_SalesTest = collect(test[:,:Other_Sales])
JP_SalesTest = collect(test[:,:JP_Sales])
Critic_ScoreTest = collect(test[:,:Critic_Score])
Critic_CountTest = collect(test[:,:Critic_Count])
User_ScoreTest = collect(test[:,:User_Score])
User_CountTest = collect(test[:,:User_Count])



for i in eachindex(Critic_CountTest) 
    if ismissing(Critic_CountTest[i]) || ismissing(Critic_ScoreTest[i]) || ismissing(User_ScoreTest[i]) || ismissing(User_CountTest[i])
        Critic_CountTest[i]= moyenneCriticCount
        Critic_ScoreTest[i]= moyenneCriticScore
        User_ScoreTest[i]= moyenneUser_Score
        User_CountTest[i]= moyenneUser_Count
    end
end

XFinal = hcat(ones(size(JP_SalesTest,1)),JP_SalesTest,Other_SalesTest, Critic_ScoreTest,Critic_CountTest, User_ScoreTest, User_CountTest)
NA_SalesTest = XFinal * Beta1Total
Global_SalesTest = XFinal * Beta2Total
predictionsCV = DataFrame(ID = test[:ID], NA_Sales = NA_SalesTest, Global_Sales = Global_SalesTest)
CSV.write("crossValidation.csv",predictionsCV)


"crossValidation.csv"